In [1]:
import numpy as np
import pandas as pd
import os
import subprocess

In [2]:
def yolo_output(img_path):
    wd = os.getcwd()
    os.chdir("/home/soham/AeroMIT/rnn_yolo_model/darknet")
    os.system("./darknet detect cfg/yolov3-tiny.cfg yolov3-tiny.weights "+img_path+">/home/soham/AeroMIT/rnn_yolo_model/darknet/result.txt")
    os.chdir(wd)

In [3]:
def result_reader(folder_path,file_name):
    wd = os.getcwd()
    os.chdir(folder_path)
    data = open(file_name,'r').read()
    os.chdir(wd)
    return data

In [4]:
def implist(data):
    imp_list = []
    first_split = data.split()
    for ele in first_split:
        if(ele[0].isdigit()==True):
            if(ele[-1] == ','):
                ele = ele.replace(",","")
            if(ele[-1] == '%'):
                ele = ele.replace("%","")
                ele = float(ele)
                ele = ele/100
            ele = float(ele)
            imp_list.append(ele)
        else:
            if(ele[-1] == ':'):
                ele = ele.replace(":","")
                imp_list.append(ele)
    imp_list = imp_list[2:len(imp_list)]
    return imp_list

In [5]:
def breaking_into_components(imp_list):
    new_implist = []
    i = 0
    while(i<len(imp_list)):
        if (i+2)<len(imp_list) and (isinstance(imp_list[i+2],(float,int))==False):
            temp1 = imp_list[i:i+2]
            random = np.random.randn(4,)
            random1 = random - random.astype(int)
            temp1 = temp1 + random1.tolist()
            new_implist.append(temp1)
            i = i+2
        else:
            temp = imp_list[i:i+6]
            i = i+6
            new_implist.append(temp)
    return new_implist

In [6]:
a = "/home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100919.png: Predicted in 0.092896 seconds. teddy bear: 61% person: 74% Bounding box:- Center_x = 0.648836, Center_y = 0.707690, Height = 0.552082, Width = 0.674658"
imp_list1 = implist(a)
print(imp_list1)
breaking_into_components(imp_list1)

['bear', 0.61, 'person', 0.74, 0.648836, 0.70769, 0.552082, 0.674658]


[['bear',
  0.61,
  0.5104182216002198,
  -0.15776009025570192,
  -0.690079943083168,
  0.5845198181091054],
 ['person', 0.74, 0.648836, 0.70769, 0.552082, 0.674658]]

In [61]:
a = [1,2]
rand = np.random.randn(4,)
print(rand.tolist())

[0.3645937982500964, -0.5334729722667566, -0.06583853042510997, -0.9991478769541502]


In [6]:
#Each grid is in the format [confidence,xpos,ypos,height,width,person, bicycle, car, motorcycle, airplane, bus, train, truck, boat, traffic light, fire hydrant, street sign, stop sign, parking meter, bench, bird, cat, dog, horse, sheep, cow, elephant, bear, zebra, giraffe, hat, backpack, umbrella, shoe, eye, glasses, handbag, tie, suitcase, frisbee, skis, snowboard, sports ball, kite, baseball bat, baseball glove, skateboard, surfboard, tennis racket, bottle, plate, wine glass, cup, fork, knife, spoon, bowl, banana, apple, sandwich, orange, broccoli, carrot, hot dog, pizza, donut, cake, chair, couch, potted plant, bed, mirror, dining table, window, desk, toilet, door, tv, laptop, mouse, remote, keyboard, cell phone, microwave, oven, toaster, sink, refrigerator, blender, book, clock, vase, scissors, teddy bear, hair drier, toothbrush, hair brush] 
def make_final3d(random_3d,imp_list):
    labels = ["person", "bicycle", "car", "motorcycle", "airplane", "bus", "train", "truck", "boat", "traffic light", "fire hydrant", "street sign", "stop sign", "parking meter", "bench", "bird", "cat", "dog", "horse", "sheep", "cow", "elephant", "bear", "zebra", "giraffe", "hat", "backpack", "umbrella", "shoe", "eye", "glasses", "handbag", "tie", "suitcase", "frisbee", "skis", "snowboard", "sports ball", "kite", "baseball bat", "baseball glove", "skateboard", "surfboard", "tennis racket", "bottle", "plate", "wine glass", "cup", "fork", "knife", "spoon", "bowl", "banana", "apple", "sandwich", "orange", "broccoli", "carrot", "hot dog", "pizza", "donut", "cake", "chair", "couch", "potted plant", "bed", "mirror", "dining table", "window", "desk", "toilet", "door", "tv", "laptop", "mouse", "remote", "keyboard", "cell phone", "microwave", "oven", "toaster", "sink", "refrigerator", "blender", "book", "clock", "vase", "scissors", "teddy bear", "hair drier", "toothbrush", "hair brush"] 
    random_3d[:,:,0] = 0
    for obj in imp_list:
        xcenter = obj[2]
        ycenter = obj[3]
        xgrid_num = int(xcenter/(1/19))
        xcenter_wrt_grid = xcenter/(1/19) - int(xcenter/(1/19))
        ygrid_num = int(ycenter/(1/19))
        ycenter_wrt_grid = ycenter/(1/19) - int(ycenter/(1/19))
        random_3d[xgrid_num,ygrid_num,0] = obj[1]
        random_3d[xgrid_num,ygrid_num,1] = xcenter_wrt_grid
        random_3d[xgrid_num,ygrid_num,2] = xcenter_wrt_grid
        random_3d[xgrid_num,ygrid_num,3] = obj[4]
        random_3d[xgrid_num,ygrid_num,4] = obj[5]
        random_3d[xgrid_num,ygrid_num,5:96] = 0
        thing_num = 0
        for thing in labels:
            if obj[0] == thing:
                random_3d[xgrid_num][ygrid_num][thing_num+5] = 1
                break
            thing_num = thing_num+1
    return random_3d

In [7]:
def add_to_df(final_flat,Yolo_preds_df):
    final_row_df = pd.DataFrame(final_flat)
    Yolo_preds_df.append(final_row_df)
    return Yolo_preds_df

In [8]:
def rnn_input(image_folder_path,image_name,result_folder_path,result_file_name):
    yolo_output(image_folder_path+'/'+image_name)
    data = result_reader(result_folder_path,result_file_name)
    imp_list = implist(data)
    new_implist = breaking_into_components(imp_list)
    random_3d = np.random.randn(19,19,96)
    random_3d = random_3d - random_3d.astype(int)
    final3d = make_final3d(random_3d,new_implist)
    final_flat = final3d.flatten()
    final_flat.reshape((final_flat.shape[0],1))
    #make the dataframe whenever u use this function before calling it
    #Yolo_preds_df = pd.DataFrame()
    #Yolo_preds_df = add_to_df(final_flat,Yolo_preds_df)
    return final_flat

In [9]:
final_flat = rnn_input("/home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl","img070.png","/home/soham/AeroMIT/rnn_yolo_model/darknet/","result.txt")
print(final_flat.shape)

(34656,)


In [ ]:
dataset_path = "/home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset"
results_file_path = "/home/soham/AeroMIT/rnn_yolo_model/darknet/result.txt"
for root1 in os.listdir(dataset_path):
    if os.path.isdir(dataset_path+'/'+root1):
        print("In directory:",dataset_path+'/'+root1)
        for root2 in os.listdir(dataset_path+'/'+root1):
            if os.path.isdir(dataset_path+'/'+root1+'/'+root2):
                print("In directory:",dataset_path+'/'+root1+'/'+root2)
                Yolo_preds_df = pd.DataFrame()
                filename_ser = []
                for filename in os.listdir(dataset_path+'/'+root1+'/'+root2):
                    print("In file:",dataset_path+'/'+root1+'/'+root2+'/'+filename)
                    if filename.endswith((".jpg",".png")):
                        filename_ser.append(filename)
                        yolo_result = rnn_input(dataset_path+'/'+root1+'/'+root2,filename,"/home/soham/AeroMIT/rnn_yolo_model/darknet/","result.txt")
                        ser = pd.Series(yolo_result)
                        Yolo_preds_df = Yolo_preds_df.append(ser,ignore_index = True)
                    #print(Yolo_preds_df)
                Yolo_preds_df['filename'] = filename_ser
                Yolo_preds_df.to_csv(dataset_path+'/'+root1+'/'+root2+'/Yolo_preds_df.csv')

In directory: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ellis_ijcv2011
In directory: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ellis_ijcv2011/track_running
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ellis_ijcv2011/track_running/input_000453.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ellis_ijcv2011/track_running/input_000384.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ellis_ijcv2011/track_running/input_000113.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ellis_ijcv2011/track_running/input_000254.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ellis_ijcv2011/track_running/input_000470.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ellis_ijcv2011/track_running/input_000165.png


In [51]:
dataset_path = "/home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko"
results_file_path = "/home/soham/AeroMIT/rnn_yolo_model/darknet/result.txt"
for root2 in os.listdir(dataset_path):
            if os.path.isdir(dataset_path+'/'+root2):
                print("In directory:",dataset_path+'/'+root2)
                Yolo_preds_df = pd.DataFrame()
                filename_ser = []
                for filename in os.listdir(dataset_path+'/'+root2):
                    print("In file:",dataset_path+'/'+root2+'/'+filename)
                    if filename.endswith((".jpg",".png")):
                        filename_ser.append(filename)
                        yolo_result = rnn_input(dataset_path+'/'+root2,filename,"/home/soham/AeroMIT/rnn_yolo_model/darknet/","result.txt")
                        ser = pd.Series(yolo_result)
                        Yolo_preds_df = Yolo_preds_df.append(ser,ignore_index = True)
                    #print(Yolo_preds_df)
                Yolo_preds_df['filename'] = filename_ser
                Yolo_preds_df.to_csv(dataset_path+'/'+root2+'/Yolo_preds_df.csv')

In directory: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00166.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00524.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00485.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00037.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00162.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00378.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00825.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00741.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00824.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00688.png
In file: /home/soh

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/groundtruth.txt
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00097.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00571.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00333.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00644.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00493.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00352.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00210.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00134.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00630.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00474.png
In file

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00287.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00607.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00246.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00771.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00375.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00682.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00805.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00737.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00204.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00038.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00190.png
In file: /

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00648.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00457.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00046.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00045.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00289.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00415.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00713.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00517.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00491.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00453.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00748.png
In file: /

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/formatted_gt.csv
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00470.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00121.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00125.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00570.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00293.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00833.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00785.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00170.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00081.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/surfer/img00060.png
In fil

...

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img152.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img245.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img215.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img307.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img257.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img194.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img303.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img345.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img007.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img327.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img292.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Tracking

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img049.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img365.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img013.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img387.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img228.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img033.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img337.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img078.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img325.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img334.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img399.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Tracking

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img058.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img117.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img386.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img017.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img251.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img300.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img043.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img144.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img191.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img067.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img415.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Tracking

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img185.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img434.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img162.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img443.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img331.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img304.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img047.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img224.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img316.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img305.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img468.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Tracking

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img440.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img412.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img323.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img318.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img446.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img370.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img232.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img061.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img465.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img289.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Babenko/girl/img481.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Tracking

In [52]:
dataset_path = "/home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross"
results_file_path = "/home/soham/AeroMIT/rnn_yolo_model/darknet/result.txt"
for root2 in os.listdir(dataset_path):
            if os.path.isdir(dataset_path+'/'+root2):
                print("In directory:",dataset_path+'/'+root2)
                Yolo_preds_df = pd.DataFrame()
                filename_ser = []
                for filename in os.listdir(dataset_path+'/'+root2):
                    print("In file:",dataset_path+'/'+root2+'/'+filename)
                    if filename.endswith((".jpg",".png")):
                        filename_ser.append(filename)
                        yolo_result = rnn_input(dataset_path+'/'+root2,filename,"/home/soham/AeroMIT/rnn_yolo_model/darknet/","result.txt")
                        ser = pd.Series(yolo_result)
                        Yolo_preds_df = Yolo_preds_df.append(ser,ignore_index = True)
                    #print(Yolo_preds_df)
                Yolo_preds_df['filename'] = filename_ser
                Yolo_preds_df.to_csv(dataset_path+'/'+root2+'/Yolo_preds_df.csv')

In directory: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000047.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000222.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000116.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000389.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000057.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000361.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000085.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000345.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000009.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000210.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000297.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000298.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000204.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000043.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000348.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000251.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000121.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000042.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000324.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000168.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000110.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Tracking

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000098.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000079.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000336.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000142.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000376.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000048.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000133.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000307.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000069.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000040.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000146.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Tracking

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000016.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000333.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000280.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000113.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000248.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000095.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000213.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000181.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000262.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000221.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000317.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Tracking

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000020.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000312.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000246.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000125.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000201.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000227.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000134.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000254.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000388.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000105.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11/00000045.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Tracking

...

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000073.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000171.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000184.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000548.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000159.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000505.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000084.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000206.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000515.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000485.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000417.png
In file: /home/soham/AeroMIT/dat

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000488.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000236.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000381.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000511.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000200.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000229.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000180.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000366.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000340.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000122.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000329.png
In file: /home/soham/AeroMIT/dat

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000559.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000188.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000393.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000023.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000243.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000143.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000263.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000004.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000223.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000247.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000452.png
In file: /home/soham/AeroMIT/dat

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000172.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000349.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000529.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000446.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000031.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000179.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000020.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000312.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000246.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000125.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis/00000201.png
In file: /home/soham/AeroMIT/dat

TypeError: ufunc 'add' did not contain a loop with signature matching types dtype('<U32') dtype('<U32') dtype('<U32')

In [ ]:
dataset_path = "/home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross"
results_file_path = "/home/soham/AeroMIT/rnn_yolo_model/darknet/result.txt"
for root2 in os.listdir(dataset_path):
            if os.path.isdir(dataset_path+'/'+root2):
                print("In directory:",dataset_path+'/'+root2)
                if root2 != 'car11' and root2 != 'trellis': 
                    Yolo_preds_df = pd.DataFrame()
                    filename_ser = []
                    for filename in os.listdir(dataset_path+'/'+root2):
                        print("In file:",dataset_path+'/'+root2+'/'+filename)
                        if filename.endswith((".jpg",".png")):
                            filename_ser.append(filename)
                            yolo_result = rnn_input(dataset_path+'/'+root2,filename,"/home/soham/AeroMIT/rnn_yolo_model/darknet/","result.txt")
                            ser = pd.Series(yolo_result)
                            Yolo_preds_df = Yolo_preds_df.append(ser,ignore_index = True)
                        #print(Yolo_preds_df)
                    Yolo_preds_df['filename'] = filename_ser
                    Yolo_preds_df.to_csv(dataset_path+'/'+root2+'/Yolo_preds_df.csv')

In directory: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/car11
In directory: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/trellis
In directory: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100479.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100070.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100394.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100917.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100399.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100025.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100260.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100084.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog10

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101225.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100262.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100265.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100383.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101112.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100648.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100766.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100382.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100221.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101288.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101238.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Tracking

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100274.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100245.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100521.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100866.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100903.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100201.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100338.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101143.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100266.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100540.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100168.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Tracking

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100341.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101236.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100878.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100774.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100610.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101042.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101321.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100975.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100353.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100746.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100253.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Tracking

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100024.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100259.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100870.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100118.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100402.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101000.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101312.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100438.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100545.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100841.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100380.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Tracking

...

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100293.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101114.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100671.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100218.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100689.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100048.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101179.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100100.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100108.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100874.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100279.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Tracking

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100022.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100757.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101200.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100811.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101127.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101202.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100979.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101006.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101299.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100972.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100666.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Tracking

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100172.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101005.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100282.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101091.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101160.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101259.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100560.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100595.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100738.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100217.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101234.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Tracking

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100788.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101327.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100233.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100247.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100845.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101072.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100781.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100333.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100342.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100327.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100431.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Tracking

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101104.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101180.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100668.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100484.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100241.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100164.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog101271.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100124.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100107.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100567.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Ross/dog1/dog100152.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Tracking

In [ ]:
dataset_path = "/home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset"
results_file_path = "/home/soham/AeroMIT/rnn_yolo_model/darknet/result.txt"
for root1 in os.listdir(dataset_path):
    if os.path.isdir(dataset_path+'/'+root1):
        if root1 != "Ellis_ijcv2011" and root1 != "Kwon_VTD" and root1 !="Ross" and root1 !="Babenko":
            print("In directory:",dataset_path+'/'+root1)
            for root2 in os.listdir(dataset_path+'/'+root1):
                if os.path.isdir(dataset_path+'/'+root1+'/'+root2):
                    print("In directory:",dataset_path+'/'+root1+'/'+root2)
                    Yolo_preds_df = pd.DataFrame()
                    filename_ser = []
                    for filename in os.listdir(dataset_path+'/'+root1+'/'+root2):
                        print("In file:",dataset_path+'/'+root1+'/'+root2+'/'+filename)
                        if filename.endswith((".jpg",".png")):
                            filename_ser.append(filename)
                            yolo_result = rnn_input(dataset_path+'/'+root1+'/'+root2,filename,"/home/soham/AeroMIT/rnn_yolo_model/darknet/","result.txt")
                            ser = pd.Series(yolo_result)
                            Yolo_preds_df = Yolo_preds_df.append(ser,ignore_index = True)
                        #print(Yolo_preds_df)
                    Yolo_preds_df['filename'] = filename_ser
                    Yolo_preds_df.to_csv(dataset_path+'/'+root1+'/'+root2+'/Yolo_preds_df.csv')

In directory: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang
In directory: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000174.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000241.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000187.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000119.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000002.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000127.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000268.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000283.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000021.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Tr

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000144.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000286.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000115.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000156.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000046.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000367.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000222.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000295.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000038.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000014.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000211.png
In file: /home/soham/

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000292.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000031.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000326.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000371.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000269.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000107.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000364.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000282.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000129.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000099.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000357.png
In file: /home/soham/

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000391.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000369.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000113.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000317.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000159.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000313.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000037.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000227.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000240.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000092.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000125.png
In file: /home/soham/

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000352.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000145.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000118.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000210.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000065.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000318.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000066.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000032.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000018.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000336.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Wang/bird_1/img-000180.png
In file: /home/soham/

...

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000260.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000013.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000174.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000187.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000212.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000085.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000200.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000080.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000219.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000076.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000186.png
In file: /home/soham/

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000184.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000159.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000084.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000206.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000153.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000188.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000242.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000170.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000153.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000095.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000164.png
In file: /home/soham/

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000073.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000170.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000148.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000240.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000192.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000253.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000194.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000056.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000229.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000028.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000120.png
In file: /home/soham/

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000247.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000211.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000245.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000179.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000169.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000194.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000039.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000011.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000008.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000123.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000135.jpg
In file: /home/soham/

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000134.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000254.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000254.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000240.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000138.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000105.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000156.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000045.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000019.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000180.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/hand2/00000166.png
In directory: /home/s

In [ ]:
dataset_path = "/home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset"
results_file_path = "/home/soham/AeroMIT/rnn_yolo_model/darknet/result.txt"
for root1 in os.listdir(dataset_path):
    if os.path.isdir(dataset_path+'/'+root1):
        if root1 != "Ellis_ijcv2011" and root1 != "Kwon_VTD" and root1 !="Ross" and root1 !="Babenko" and root1 != 'Wang' and root1 != 'Thang' and root1 != 'Other':
            print("In directory:",dataset_path+'/'+root1)
            for root2 in os.listdir(dataset_path+'/'+root1):
                if os.path.isdir(dataset_path+'/'+root1+'/'+root2):
                    if root2 != 'dinosaur' and root2 != 'gymnastics' and root2!= 'hand2':
                        print("In directory:",dataset_path+'/'+root1+'/'+root2)
                        Yolo_preds_df = pd.DataFrame()
                        filename_ser = []
                        for filename in os.listdir(dataset_path+'/'+root1+'/'+root2):
                            print("In file:",dataset_path+'/'+root1+'/'+root2+'/'+filename)
                            if filename.endswith((".jpg",".png")):
                                filename_ser.append(filename)
                                yolo_result = rnn_input(dataset_path+'/'+root1+'/'+root2,filename,"/home/soham/AeroMIT/rnn_yolo_model/darknet/","result.txt")
                                ser = pd.Series(yolo_result)
                                Yolo_preds_df = Yolo_preds_df.append(ser,ignore_index = True)
                            #print(Yolo_preds_df)
                        Yolo_preds_df['filename'] = filename_ser
                        Yolo_preds_df.to_csv(dataset_path+'/'+root1+'/'+root2+'/Yolo_preds_df.csv')

In directory: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin
In directory: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000139.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000047.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000041.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000048.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000222.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000116.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000057.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000140.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000069.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yo

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000046.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000007.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000021.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000108.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000101.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000104.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000249.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000232.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000052.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000031.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000036.jpg
In file: /home/soham/

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000241.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000117.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000076.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000005.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000071.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000233.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000148.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000093.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000040.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000045.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000203.png
In file: /home/soham/

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000100.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000203.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000233.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000064.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000050.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000103.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000058.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000034.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000264.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000108.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000097.png
In file: /home/soham/

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000070.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000217.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000182.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000049.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000017.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000092.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000044.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000055.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000252.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000172.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Cehovin/torus/00000145.png
In file: /home/soham/

...

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0493.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0456.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0569.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0380.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0523.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0015.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0209.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0085.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0014.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0507.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0527.jpg

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0232.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0577.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0473.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0073.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0386.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0267.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0035.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0041.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0454.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0430.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0213.png

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0275.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0307.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0450.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0015.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0021.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0271.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0282.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0019.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0309.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0180.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0032.jpg

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0425.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0017.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0106.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0072.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0536.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0327.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0076.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0119.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0133.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0329.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0367.jpg

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0387.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0341.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0108.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0349.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0080.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0512.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0372.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0279.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0441.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0314.png
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/BoBot/Vid_A_ball/img0519.jpg

In [9]:
formatteddataset_path = "/home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset"
results_file_path = "/home/soham/AeroMIT/rnn_yolo_model/darknet/result.txt"
for root1 in os.listdir(dataset_path):
    if os.path.isdir(dataset_path+'/'+root1):
        if root1 != "Ellis_ijcv2011" and root1 != "Kwon_VTD" and root1 !="Ross" and root1 !="Babenko" and root1 != 'Wang' and root1 != 'Thang' and root1 != 'Other' and root1 != 'Cehovin' and root1 != 'BoBot':
            print("In directory:",dataset_path+'/'+root1)
            for root2 in os.listdir(dataset_path+'/'+root1):
                if os.path.isdir(dataset_path+'/'+root1+'/'+root2):
                    if root2:
                        print("In directory:",dataset_path+'/'+root1+'/'+root2)
                        Yolo_preds_df = pd.DataFrame()
                        filename_ser = []
                        for filename in os.listdir(dataset_path+'/'+root1+'/'+root2):
                            print("In file:",dataset_path+'/'+root1+'/'+root2+'/'+filename)
                            if filename.endswith((".jpg",".png")):
                                filename_ser.append(filename)
                                yolo_result = rnn_input(dataset_path+'/'+root1+'/'+root2,filename,"/home/soham/AeroMIT/rnn_yolo_model/darknet/","result.txt")
                                ser = pd.Series(yolo_result)
                                Yolo_preds_df = Yolo_preds_df.append(ser,ignore_index = True)
                            #print(Yolo_preds_df)
                        Yolo_preds_df['filename'] = filename_ser
                        Yolo_preds_df.to_csv(dataset_path+'/'+root1+'/'+root2+'/Yolo_preds_df.csv')

In directory: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal
In directory: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2144.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2143.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2296.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2237.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2220.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2212.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2256.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2208.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingData

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2051.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2319.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2096.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2284.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2071.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2177.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2097.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2089.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2259.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2241.jpg
In file: /home/soham

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2039.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2227.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2199.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2132.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2203.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2087.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2159.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2260.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2152.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2246.jpg
In file: /home/soham

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2040.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2187.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2295.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2070.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2328.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2248.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2326.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2141.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2009.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2011.jpg
In file: /home/soham

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2042.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2037.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2292.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2098.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2016.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2318.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/pedestrian4/uavperson2167.jpg
In directory: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/david
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/david/00000139.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Kalal/david/00000587.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset

...

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0356.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0206.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0003.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0192.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0011.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0182.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0245.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0129.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0296.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0253.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Trac

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0441.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0248.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0230.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0469.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0410.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0337.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0346.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0493.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0436.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0306.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Trac

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0262.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0370.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0418.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0259.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0050.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0260.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0455.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0473.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0313.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0404.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Trac

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0021.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0037.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0293.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0278.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0082.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0236.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0167.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0425.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0138.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0363.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Trac

In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0140.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0393.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0255.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0348.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0413.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0225.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0151.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0332.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0224.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/TrackingDataset/Godec/volleyball/beach1-0254.jpg
In file: /home/soham/AeroMIT/dataset_rnn_yolo/Trac